**Discrete Event simulation for Take Home 2 of 4DM40**

In [ ]:
# =================================
# Imports
# =================================
from PyCh import *
import matlab.engine
import numpy as np


# =================================
# Simulation parameters
# =================================
batchsizeWS2  = 10                                          # maximum batchsize of Workstation 2
EPTsWS1       = [ (84.0, 1.0), (56.0, 1.0), (42.0, 1.0) ]   # list with (te,ce) of wip-dependent EPT-distributions
EPTsWS2       = [ (525.0, 1.0) ]
EPTsWS3       = [ (35.0, 1.0) ]
initialmemory = [0 for i in range(4)]                       # initial memory needed for determining control action
                                                            # for this example: targets from previous shift
tfinish       = 2628000.0                                   # end of simulation time (5 years, expressed in minutes)
tsample       = 360.0                                       # sample time (i.e., duration of shift in minutes)
outputfname   = "Takehome2_output.txt"                      # filename for simulation output


# ====================================================
# Functions and processes for simulation
#
# There should be no need for editing the code below
# ====================================================
def save_results_to_file(ts, xs, us):
    """
    Save the output of the simulation (sample times, buffer contents, inputs) to file
    
    @param ts: sample times
    @type  ts: C{list} of C{int}
    
    @param xs: buffer contents at sample times (start counting at 1)
    @type  xs: C{list} of C{list} of C{int}
    
    @param us: inputs at sample times (start counting at 0)
    @type  us: C{list} of C{list} of C{int}
    """
    f = open(outputfname,"w")
    f.write(str(ts)[1:-1]+'\n')
    for i in range(len(xs)):
        f.write(str(xs[i])[1:-1]+'\n')
    for i in range(len(us)):
        f.write(str(us[i])[1:-1]+'\n')
    f.close()
    
def Model():
    """
    Defines and runs the discrete event simulation model
    """
    # define environment
    env = Environment()
    # define channels
    a = Channel(env)
    b = Channel(env)
    c = Channel(env)
    d = Channel(env)
    p = [Channel(env) for i in range(5)]
    q = [Channel(env) for i in range(4)]
    # define processes
    G = Generator(env,a,p[4])
    W1 = Workstation(env,a,b,p[0],q[0],EPTsWS1,1)
    W2 = Workstation(env,b,c,p[1],q[1],EPTsWS2,batchsizeWS2)
    W3 = Workstation(env,c,d,p[2],q[2],EPTsWS3,1)
    E = Exit(env,d,p[3],q[3])
    CC = Controller(env,q,p)
    # run simulation environment
    env.run(until=CC)
    
@process
def Generator(env, c_out, req_in):
    """
    Generator process:
    Generates lots as soon as it receives a target for the new shift from the controller
    """
    target = 0
    while True:
        sending = c_out.send([env.time]) if target>0 else None
        reqreceiving = req_in.receive()
        x = yield env.select(sending, reqreceiving)
        if selected(sending):
            target = target - 1
        if selected(reqreceiving):
            target = x
        
@process
def Workstation(env, c_in, c_out, req_in, req_out, EPTs, bs):
    """
    Workstation process:
    Consists of a Buffer and a Server.
    
    @param EPTs: List with (te,ce) pairs for wip-dependent EPT-distributions of Server
    @type  EPTs: C{list} of (C{real},C{real})
    
    @param bs: batch size of Server
    @type  bs: C{int}
    
    """
    c_bm = Channel(env)
    B = Buffer(env, c_in, c_bm, req_in, req_out, bs)
    S = Server(env, c_bm, c_out, EPTs)
    yield B
    yield S
    
@process
def Buffer(env, c_in, c_out, req_in, req_out, bs):
    """
    Buffer process:
    Adds received batches in list xs, informs controller about number of batches available in buffer upon request
    after which it receives production targets for the upcoming shift, and sends out batches (never more than the
    the shift-target) together with the current number of batches remaining in the buffer.
    
    @param bs: batch size of Server
    @type  bs: C{int}
    
    """
    xs = []
    target = 0
    while True:
        amount = min(bs,target)
        sending = c_out.send((xs[0:amount],(len(xs)-1)//bs)) if (amount>0 and len(xs)>=amount) else None
        receiving = c_in.receive()
        reqreceiving = req_in.receive()
        x = yield env.select(sending, receiving, reqreceiving)
        if selected(receiving):
            xs = xs + x
        if selected(sending):
            xs = xs[amount:]
            target = target - amount
        if selected(reqreceiving):
            yield env.execute(req_out.send(len(xs)))
            target = yield env.execute(req_in.receive())
    
@process
def Server(env, c_in, c_out, EPTs):
    """
    Server process:
    Receives batch together with the number of batches in buffer. Based on the latter, selects the EPT-distribution
    to use for determining the processing time, after which the processed batch is sent out.
    If the wip in the workstation is larger than the number of EPT-distributions available in the list, the last
    EPT-distribution is used.
    
    @param EPTs: List with (te,ce) pairs for wip-dependent EPT-distributions of Server
    @type  EPTs: C{list} of (C{real},C{real})
    
    """
    u = [lambda: random.gamma(1/(ca*ca),ca*ca*ta) for (ta,ca) in EPTs]
    maxindex=len(u)-1
    while True:
        (lots,index) = yield env.execute(c_in.receive())
        delay = u[min(index,maxindex)]()
        yield env.timeout(delay)
        yield env.execute(c_out.send(lots))
    
@process
def Exit(env, c_in, req_in, req_out):
    """
    Exit process:
    Collects all jobs leaving the system and communicates the cumulative production to the controller upon request.
    Also determines the mean flow time of jobs, though that information is not outputted.
    
    """
    n = 0
    meanflowtime = 0.0
    while True:
        receiving = c_in.receive()
        reqreceiving = req_in.receive()
        xs = yield env.select(receiving, reqreceiving)
        if selected(receiving):
            for x in xs:
                flowtime = env.now - x
                n = n + 1
                meanflowtime = (n-1)/n * meanflowtime + flowtime/n
                print(f"Mean flowtime (in minutes): {meanflowtime:f}; mean Throughput (in lots per shift): {n*tsample/env.now:f}.")
        if selected(reqreceiving):
            yield env.execute(req_out.send(n))

@process
def Controller(env, c_in, c_out):
    """
    Controller process:
    Every sample time, query all Workstations, as well as the Exit process, for the buffer contents and the
    cumulative production of the line. Then call the MATLAB-function uMPC.m to determine the targets for
    the Generator and Workstations. Finally, communicate the new targets (rounded to nearest integer) to Generator
    and Workstations.
    As the MPC used for controlling the system might want to use information about previous time steps
    the variable memory is used for collecting that information.
    All information about sample times, buffer contents and targets are collected and saved to file.
    """
    eng = matlab.engine.start_matlab()
    n = len(c_in)
    ts = []
    bcs = [ [] for i in range(n)]
    us = [ [] for i in range(n)]
    memory = initialmemory
    while env.time<tfinish:
        print(f"Time: {env.time}")
        # send a request (for the current buffer contents) to each workstation
        for i in range(n):
            yield env.execute(c_out[i].send(None))
        # receive the current amount of jobs in the buffer for each workstation
        ts = ts + [env.time] # save time for plotting
        bc = [] # set current buffer contents to empty list
        for i in range(n):
            buffercount = yield env.execute(c_in[i].receive())
            bc = bc + [buffercount] # add to list with buffer contents
            bcs[i] = bcs[i] + [buffercount] # save buffer contents for plotting
        # determine new targets
        (engtargets,engmemory,engexitflag) = eng.uMPC(env.time,bc,memory,nargout=3)
        # convert to correct Python types; also round targets to nearest integer.
        targets = [ round(el[0]) for el in np.array(engtargets) ]
        memory = [ round(el[0]) for el in np.array(engmemory) ]
        exitflag = int(engexitflag)
        # provide warning if exitflag is set
        if exitflag != 1:
            print(f"Warning: at time {env.time}: EXITFLAG={exitflag}. Most likely solver produced wrong targets.")
        # send new targets to workstations
        for i in range(n):
            us[i] = us[i] + [targets[i]] # save targets for plotting
            if i<n-1:
                yield env.execute(c_out[i].send(targets[i+1])) # send targets to workstations
            yield env.execute(c_out[n].send(targets[0])) # send target to generator
            
        # wait for the duration of sample time (i.e., shift duration)
        yield env.timeout(tsample)
    eng.quit()
    save_results_to_file(ts,bcs,us)

    
# call Model with required parameters
Model()
print("Simulation completed")

PyCh version 2.2 imported successfully.
 
Time: 0
Time: 360.0
Time: 720.0
Mean flowtime (in minutes): 884.651598; mean Throughput (in lots per shift): 0.406940.
Mean flowtime (in minutes): 927.435519; mean Throughput (in lots per shift): 0.742100.
Mean flowtime (in minutes): 947.221806; mean Throughput (in lots per shift): 1.094453.
Mean flowtime (in minutes): 960.820606; mean Throughput (in lots per shift): 1.437675.
Time: 1080.0
Mean flowtime (in minutes): 986.044197; mean Throughput (in lots per shift): 1.656027.
Mean flowtime (in minutes): 1003.114925; mean Throughput (in lots per shift): 1.984439.
Mean flowtime (in minutes): 1019.028202; mean Throughput (in lots per shift): 2.261088.
Mean flowtime (in minutes): 1031.644992; mean Throughput (in lots per shift): 2.571515.
Mean flowtime (in minutes): 1041.664510; mean Throughput (in lots per shift): 2.888162.
Mean flowtime (in minutes): 1049.715062; mean Throughput (in lots per shift): 3.208070.
Time: 1440.0
Time: 1800.0
Mean flowtim

Mean flowtime (in minutes): 3929.049022; mean Throughput (in lots per shift): 4.001408.
Mean flowtime (in minutes): 3929.158467; mean Throughput (in lots per shift): 4.002338.
Mean flowtime (in minutes): 3929.302738; mean Throughput (in lots per shift): 4.003853.
Mean flowtime (in minutes): 3929.180936; mean Throughput (in lots per shift): 4.006470.
Time: 117360.0
Mean flowtime (in minutes): 3929.223324; mean Throughput (in lots per shift): 4.002232.
Mean flowtime (in minutes): 3929.344382; mean Throughput (in lots per shift): 4.001793.
Mean flowtime (in minutes): 3929.200872; mean Throughput (in lots per shift): 4.004365.
Mean flowtime (in minutes): 3929.120648; mean Throughput (in lots per shift): 4.004617.
Time: 117720.0
Mean flowtime (in minutes): 3929.161429; mean Throughput (in lots per shift): 4.002293.
Mean flowtime (in minutes): 3929.241359; mean Throughput (in lots per shift): 4.003604.
Mean flowtime (in minutes): 3929.321460; mean Throughput (in lots per shift): 4.006647.
Me

Time: 126360.0
Time: 126720.0
Time: 127080.0
Time: 127440.0
Time: 127800.0
Mean flowtime (in minutes): 3894.324940; mean Throughput (in lots per shift): 3.933634.
Mean flowtime (in minutes): 3895.571706; mean Throughput (in lots per shift): 3.936276.
Mean flowtime (in minutes): 3896.581967; mean Throughput (in lots per shift): 3.938130.
Mean flowtime (in minutes): 3897.592043; mean Throughput (in lots per shift): 3.940886.
Mean flowtime (in minutes): 3898.605141; mean Throughput (in lots per shift): 3.943505.
Mean flowtime (in minutes): 3899.389823; mean Throughput (in lots per shift): 3.945042.
Time: 128160.0
Mean flowtime (in minutes): 3900.214506; mean Throughput (in lots per shift): 3.946073.
Mean flowtime (in minutes): 3901.043847; mean Throughput (in lots per shift): 3.948629.
Mean flowtime (in minutes): 3901.893603; mean Throughput (in lots per shift): 3.950501.
Time: 128520.0
Time: 128880.0
Time: 129240.0
Mean flowtime (in minutes): 3903.681068; mean Throughput (in lots per shi

Time: 135000.0
Mean flowtime (in minutes): 3954.240641; mean Throughput (in lots per shift): 3.973065.
Mean flowtime (in minutes): 3954.813041; mean Throughput (in lots per shift): 3.974890.
Mean flowtime (in minutes): 3955.454464; mean Throughput (in lots per shift): 3.974490.
Mean flowtime (in minutes): 3956.119084; mean Throughput (in lots per shift): 3.976095.
Mean flowtime (in minutes): 3956.591487; mean Throughput (in lots per shift): 3.976582.
Time: 135360.0
Mean flowtime (in minutes): 3957.098265; mean Throughput (in lots per shift): 3.977703.
Mean flowtime (in minutes): 3957.607370; mean Throughput (in lots per shift): 3.980229.
Mean flowtime (in minutes): 3958.118810; mean Throughput (in lots per shift): 3.982755.
Mean flowtime (in minutes): 3958.396448; mean Throughput (in lots per shift): 3.985104.
Mean flowtime (in minutes): 3958.695337; mean Throughput (in lots per shift): 3.986807.
Mean flowtime (in minutes): 3959.031469; mean Throughput (in lots per shift): 3.987802.
Me

Mean flowtime (in minutes): 4005.206286; mean Throughput (in lots per shift): 4.000032.
Mean flowtime (in minutes): 4004.596636; mean Throughput (in lots per shift): 4.002239.
Mean flowtime (in minutes): 4003.994028; mean Throughput (in lots per shift): 4.004326.
Mean flowtime (in minutes): 4003.409465; mean Throughput (in lots per shift): 4.005921.
Time: 152280.0
Mean flowtime (in minutes): 4002.971266; mean Throughput (in lots per shift): 4.001798.
Mean flowtime (in minutes): 4002.341193; mean Throughput (in lots per shift): 4.003266.
Mean flowtime (in minutes): 4001.733695; mean Throughput (in lots per shift): 4.004656.
Mean flowtime (in minutes): 4001.165063; mean Throughput (in lots per shift): 4.005318.
Time: 152640.0
Mean flowtime (in minutes): 4000.737736; mean Throughput (in lots per shift): 4.001415.
Mean flowtime (in minutes): 4000.329486; mean Throughput (in lots per shift): 4.002946.
Mean flowtime (in minutes): 3999.721382; mean Throughput (in lots per shift): 4.004789.
Me

...

Mean flowtime (in minutes): 3757.188050; mean Throughput (in lots per shift): 3.999423.
Mean flowtime (in minutes): 3757.185207; mean Throughput (in lots per shift): 3.999463.
Mean flowtime (in minutes): 3757.182377; mean Throughput (in lots per shift): 3.999602.
Mean flowtime (in minutes): 3757.182172; mean Throughput (in lots per shift): 3.999625.
Mean flowtime (in minutes): 3757.182938; mean Throughput (in lots per shift): 3.999722.
Mean flowtime (in minutes): 3757.172208; mean Throughput (in lots per shift): 3.999814.
Mean flowtime (in minutes): 3757.161971; mean Throughput (in lots per shift): 3.999932.
Mean flowtime (in minutes): 3757.152702; mean Throughput (in lots per shift): 4.000028.
Mean flowtime (in minutes): 3757.143470; mean Throughput (in lots per shift): 4.000166.
Mean flowtime (in minutes): 3757.134286; mean Throughput (in lots per shift): 4.000304.
Time: 2576880.0
Mean flowtime (in minutes): 3757.116587; mean Throughput (in lots per shift): 4.000263.
Mean flowtime (i

Mean flowtime (in minutes): 3756.205148; mean Throughput (in lots per shift): 4.000100.
Mean flowtime (in minutes): 3756.177952; mean Throughput (in lots per shift): 4.000132.
Mean flowtime (in minutes): 3756.154167; mean Throughput (in lots per shift): 4.000119.
Mean flowtime (in minutes): 3756.119132; mean Throughput (in lots per shift): 4.000202.
Time: 2585880.0
Mean flowtime (in minutes): 3756.089193; mean Throughput (in lots per shift): 4.000115.
Mean flowtime (in minutes): 3756.059963; mean Throughput (in lots per shift): 4.000222.
Mean flowtime (in minutes): 3756.031831; mean Throughput (in lots per shift): 4.000313.
Mean flowtime (in minutes): 3756.005944; mean Throughput (in lots per shift): 4.000352.
Time: 2586240.0
Mean flowtime (in minutes): 3755.988856; mean Throughput (in lots per shift): 4.000101.
Mean flowtime (in minutes): 3755.972272; mean Throughput (in lots per shift): 4.000217.
Mean flowtime (in minutes): 3755.959935; mean Throughput (in lots per shift): 4.000168.


Time: 2604960.0
Time: 2605320.0
Mean flowtime (in minutes): 3759.507471; mean Throughput (in lots per shift): 3.994848.
Mean flowtime (in minutes): 3759.596572; mean Throughput (in lots per shift): 3.994971.
Mean flowtime (in minutes): 3759.689217; mean Throughput (in lots per shift): 3.994952.
Time: 2605680.0
Mean flowtime (in minutes): 3759.783573; mean Throughput (in lots per shift): 3.995014.
Mean flowtime (in minutes): 3759.878326; mean Throughput (in lots per shift): 3.995134.
Mean flowtime (in minutes): 3759.960890; mean Throughput (in lots per shift): 3.995260.
Mean flowtime (in minutes): 3760.043910; mean Throughput (in lots per shift): 3.995378.
Mean flowtime (in minutes): 3760.127037; mean Throughput (in lots per shift): 3.995511.
Mean flowtime (in minutes): 3760.197724; mean Throughput (in lots per shift): 3.995649.
Mean flowtime (in minutes): 3760.268671; mean Throughput (in lots per shift): 3.995775.
Mean flowtime (in minutes): 3760.337023; mean Throughput (in lots per sh

Mean flowtime (in minutes): 3765.690939; mean Throughput (in lots per shift): 4.000119.
Mean flowtime (in minutes): 3765.698798; mean Throughput (in lots per shift): 4.000224.
Mean flowtime (in minutes): 3765.694355; mean Throughput (in lots per shift): 4.000357.
Mean flowtime (in minutes): 3765.690981; mean Throughput (in lots per shift): 4.000447.
Time: 2613960.0
Mean flowtime (in minutes): 3765.701378; mean Throughput (in lots per shift): 3.999973.
Mean flowtime (in minutes): 3765.699391; mean Throughput (in lots per shift): 4.000110.
Time: 2614320.0
Mean flowtime (in minutes): 3765.707598; mean Throughput (in lots per shift): 3.999795.
Mean flowtime (in minutes): 3765.716140; mean Throughput (in lots per shift): 3.999918.
Mean flowtime (in minutes): 3765.726274; mean Throughput (in lots per shift): 3.999985.
Mean flowtime (in minutes): 3765.736616; mean Throughput (in lots per shift): 4.000113.
Mean flowtime (in minutes): 3765.737447; mean Throughput (in lots per shift): 4.000123.


Mean flowtime (in minutes): 3764.115026; mean Throughput (in lots per shift): 4.000112.
Mean flowtime (in minutes): 3764.086141; mean Throughput (in lots per shift): 4.000210.
Mean flowtime (in minutes): 3764.046555; mean Throughput (in lots per shift): 4.000274.
Mean flowtime (in minutes): 3764.010085; mean Throughput (in lots per shift): 4.000273.
Time: 2623320.0
Mean flowtime (in minutes): 3763.981171; mean Throughput (in lots per shift): 4.000074.
Mean flowtime (in minutes): 3763.952465; mean Throughput (in lots per shift): 4.000202.
Mean flowtime (in minutes): 3763.925501; mean Throughput (in lots per shift): 4.000262.
Mean flowtime (in minutes): 3763.899736; mean Throughput (in lots per shift): 4.000346.
Time: 2623680.0
Mean flowtime (in minutes): 3763.869707; mean Throughput (in lots per shift): 4.000124.
Mean flowtime (in minutes): 3763.840032; mean Throughput (in lots per shift): 4.000246.
Mean flowtime (in minutes): 3763.810765; mean Throughput (in lots per shift): 4.000365.
